In [10]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
!pip install geocoder
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

print("Libraries have been imported.")

Libraries have been imported.


In [23]:
website_text = requests.get("https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago").text
soup = BeautifulSoup(website_text,'xml')
table = soup.find('table',{'class':'wikitable sortable'})

In [26]:
# obtain info from the table
table_rows = table.find_all('tr')
data = []
for row in table_rows:
    td=[]
    for t in row.find_all('td'):
        td.append(t.text.strip())
    data.append(td)
chicago_df = pd.DataFrame(data, columns=['Neighborhood', 'Community Area'])

In [29]:
chicago_df.head()

Neighborhood  Community Area
0             None            None
1      Albany Park     Albany Park
2  Altgeld Gardens       Riverdale
3    Andersonville       Edgewater
4   Archer Heights  Archer Heights

In [30]:
# Obtain coordinates of each neighborhood

# define a function to get coordinates
def get_latlng(neighborhood):
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Chicago, United States'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

coords = [ get_latlng(neighborhood) for neighborhood in chicago_df["Neighborhood"].tolist() ]

df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

# merge the coordinates into the original dataframe
chicago_df['Latitude'] = df_coords['Latitude']
chicago_df['Longitude'] = df_coords['Longitude']


# check the neighborhoods and the coordinates
print(chicago_df.shape)
chicago_df.head()

(247, 4)


Neighborhood  Community Area  Latitude  Longitude
0             None            None  41.88425  -87.63245
1      Albany Park     Albany Park  41.96829  -87.72338
2  Altgeld Gardens       Riverdale  41.65441  -87.60225
3    Andersonville       Edgewater  41.98046  -87.66834
4   Archer Heights  Archer Heights  41.81154  -87.72556

In [32]:
# save as CSV file
chicago_df.to_csv("chicago_neighborhoods.csv", index=False)

In [33]:
address = 'Chicago'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(latitude, longitude))

C:\Users\David\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of Chicago are 41.8755616, -87.6244212.


In [34]:
# create map of Chicago using latitude and longitude values
map_chicago = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(chicago_df['Latitude'], chicago_df['Longitude'], chicago_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_chicago)  
    
map_chicago

In [35]:
CLIENT_ID = 'SWGNGR0J13NJO1NSZ43LUR5NHFLQHXRQETMWAEWX31OWHQXE' # Foursquare ID
CLIENT_SECRET = 'YX1RAO3NOG32HTD5X1N5KFSWD3ITRIFUANLQM2WTM2TEJ0FI' # Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('My credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentails:
CLIENT_ID: SWGNGR0J13NJO1NSZ43LUR5NHFLQHXRQETMWAEWX31OWHQXE
CLIENT_SECRET:YX1RAO3NOG32HTD5X1N5KFSWD3ITRIFUANLQM2WTM2TEJ0FI


In [38]:
def getNearbyVenues(names, latitudes, longitudes,radius=500):
    LIMIT = 100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [39]:
chicago_venues = getNearbyVenues(names=chicago_df['Neighborhood'],
                                   latitudes=chicago_df['Latitude'],
                                   longitudes=chicago_df['Longitude']
                                  )

None
Albany Park
Altgeld Gardens
Andersonville
Archer Heights
Armour Square
Ashburn
Ashburn Estates
Auburn Gresham
Avalon Park
Avondale
Avondale Gardens
Back of the Yards
Belmont Central
Belmont Gardens
Belmont Heights
Belmont Terrace
Beverly
Beverly View
Beverly Woods
Big Oaks
Boystown
Bowmanville
Brainerd
Brickyard
Bridgeport
Brighton Park
Bronzeville
Bucktown
Budlong Woods
Buena Park
Burnside
Cabrini–Green
Calumet Heights
Canaryville
Central Station
Chatham
Chicago Lawn
Chinatown
Chrysler Village
Clarendon Park
Clearing East
Clearing West
Cottage Grove Heights
Cragin
Crestline
Dearborn Homes
Dearborn Park
Douglas Park
Dunning
East Beverly
East Chatham
East Garfield Park
East Hyde Park
East Pilsen
East Side
East Village
Eden Green
Edgebrook
Edgewater
Edgewater Beach
Edgewater Glen
Edison Park
Englewood
Fernwood
Fifth City
Ford City
Forest Glen
Fuller Park
Fulton River District
Gage Park
Galewood
The Gap
Garfield Ridge
Gladstone Park
Gold Coast
Golden Gate
Goose Island
Graceland West


In [40]:
chicago_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         None               41.88425               -87.63245   
1         None               41.88425               -87.63245   
2         None               41.88425               -87.63245   
3         None               41.88425               -87.63245   
4         None               41.88425               -87.63245   

                       Venue  Venue Latitude  Venue Longitude  \
0                  Starbucks       41.884298       -87.633851   
1    Cadillac Palace Theatre       41.884006       -87.633144   
2             Luke's Lobster       41.884120       -87.632375   
3    Do-Rite Donuts & Coffee       41.884598       -87.629904   
4  Roti Modern Mediterranean       41.884605       -87.634155   

             Venue Category  
0               Coffee Shop  
1                   Theater  
2        Seafood Restaurant  
3                Donut Shop  
4  Mediterranean Restaurant

In [41]:
chicago_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                 
Albany Park                                             25   
Altgeld Gardens                                          1   
Andersonville                                           55   
Archer Heights                                          22   
Armour Square                                           18   
Ashburn                                                  6   
Ashburn Estates                                          6   
Auburn Gresham                                           4   
Avalon Park                                             16   
Avondale                                                30   
Avondale Gardens                                         4   
Back of the Yards                                       17   
Belmont Central                                         17   
Belmont Gardens                                         28   
Belmont Heights                                         28   
Belmont Terrace                                         28   
Beverly                                                  4   
Beverly View                                            12   
Beverly Woods                                            9   
Big Oaks                                               100   
Bowmanville                                              9   
Boystown                                                56   
Brainerd                                                 6   
Brickyard                                               43   
Bridgeport                                              34   
Brighton Park                                           16   
Bronzeville                                              8   
Bucktown                                                39   
Budlong Woods                                          100   
Buena Park                                              45   
Burnside                                                 4   
Cabrini–Green                                           43   
Calumet Heights                                          8   
Canaryville                                             10   
Central Station                                          3   
Chatham                                                  7   
Chicago Lawn                                            17   
Chinatown                                               51   
Chrysler Village                                        16   
Clarendon Park                                          43   
Clearing East                                           12   
Clearing West                                           12   
Cottage Grove Heights                                    4   
Cragin                                                  12   
Crestline                                                7   
Dearborn Homes                                          17   
Dearborn Park                                           65   
Douglas Park                                             4   
Dunning                                                  4   
East Beverly                                            12   
East Chatham                                             7   
East Garfield Park                                      10   
East Hyde Park                                          30   
East Pilsen                                             59   
East Side                                                6   
East Village                                            69   
Eden Green                                               7   
Edgebrook                                               23   
Edgewater                                               42   
Edgewater Beach                                         42   
Edgewater Glen                                          47   
Edison Park                                              4   
Englewood                                               16   
Fernwoo

In [42]:
print('There are {} uniques categories.'.format(len(chicago_venues['Venue Category'].unique())))

There are 360 uniques categories.


In [43]:
# one hot encoding
chicago_onehot = pd.get_dummies(chicago_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
chicago_onehot['Neighborhood'] = chicago_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [chicago_onehot.columns[-1]] + list(chicago_onehot.columns[:-1])
chicago_onehot = chicago_onehot[fixed_columns]

chicago_onehot.head()

Zoo Exhibit  ATM  Accessories Store  Afghan Restaurant  African Restaurant  \
0            0    0                  0                  0                   0   
1            0    0                  0                  0                   0   
2            0    0                  0                  0                   0   
3            0    0                  0                  0                   0   
4            0    0                  0                  0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  American Restaurant  Amphitheater  Antique Shop  Arcade  \
0                 0                    0             0             0       0   
1                 0                    0             0             0       0   
2                 0                    0             0             0       0   
3                 0                    0             0             0       0   
4                 0                    0             0             0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Auto Dealership  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0                0                0          0           0           0   
1                0                0          0           0           0   
2                0                0          0           0           0   
3                0                0          0           0           0   
4                0                0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0                0         0            0           0              0   
1      0                0         0            0           0              0   
2      0                0         0            0           0              0   
3      0                0         0            0           0              0   
4      0                0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0     

In [44]:
chicago_onehot.shape

(6542, 360)

In [112]:
chicago_grouped = chicago_onehot.groupby('Neighborhood').mean().reset_index()
chicago_grouped

Neighborhood  Zoo Exhibit       ATM  \
0                            Albany Park     0.000000  0.000000   
1                        Altgeld Gardens     0.000000  0.000000   
2                          Andersonville     0.000000  0.000000   
3                         Archer Heights     0.000000  0.000000   
4                          Armour Square     0.000000  0.000000   
5                                Ashburn     0.000000  0.000000   
6                        Ashburn Estates     0.000000  0.000000   
7                         Auburn Gresham     0.000000  0.000000   
8                            Avalon Park     0.000000  0.062500   
9                               Avondale     0.000000  0.000000   
10                      Avondale Gardens     0.000000  0.000000   
11                     Back of the Yards     0.000000  0.000000   
12                       Belmont Central     0.000000  0.000000   
13                       Belmont Gardens     0.000000  0.000000   
14                       Belmont Heights     0.000000  0.000000   
15                       Belmont Terrace     0.000000  0.000000   
16                               Beverly     0.000000  0.000000   
17                          Beverly View     0.000000  0.000000   
18                         Beverly Woods     0.000000  0.000000   
19                              Big Oaks     0.000000  0.000000   
20                           Bowmanville     0.000000  0.000000   
21                              Boystown     0.000000  0.000000   
22                              Brainerd     0.000000  0.000000   
23                             Brickyard     0.000000  0.000000   
24                            Bridgeport     0.000000  0.000000   
25                         Brighton Park     0.000000  0.000000   
26                           Bronzeville     0.000000  0.000000   
27                              Bucktown     0.000000  0.000000   
28                         Budlong Woods     0.000000  0.000000   
29                            Buena Park     0.000000  0.000000   
30                              Burnside     0.000000  0.000000   
31                         Cabrini–Green     0.000000  0.000000   
32                       Calumet Heights     0.000000  0.000000   
33                           Canaryville     0.000000  0.000000   
34                       Central Station     0.000000  0.000000   
35                               Chatham     0.000000  0.000000   
36                          Chicago Lawn     0.000000  0.000000   
37                             Chinatown     0.000000  0.000000   
38                      Chrysler Village     0.000000  0.000000   
39                        Clarendon Park     0.000000  0.000000   
40                         Clearing East     0.000000  0.000000   
41                         Clearing West     0.000000  0.000000   
42                 Cottage Grove Heights     0.000000  0.000000   
43                                Cragin     0.000000  0.000000   
44                             Crestline     0.000000  0.000000   
45                        Dearborn Homes     0.000000  0.000000   
46                         Dearborn Park     0.000000  0.000000   
47                          Douglas Park     0.000000  0.000000   
48                               Dunning     0.000000  0.000000   
49                          East Beverly     0.000000  0.000000   
50                          East Chatham     0.000000  0.000000   
51                    East Garfield Park     0.000000  0.000000   
52                        East Hyde Park     0.000000  0.000000   
53                           East Pilsen     0.000000  0.000000   
54                             East Side     0.000000  0.000000   
55                          East Village     0.000000  0.000000   
56                            Eden Green     0.000000  0.000000   
57                             Edgebrook     0.000000  0.000000   
58                             Edgewater     0.000000  0.000000   
59      

In [118]:
len(chicago_grouped[chicago_grouped["Mexican Restaurant"] > 0])
chicago_new = chicago_grouped[["Neighborhood","Mexican Restaurant"]]
chicago_new

Neighborhood  Mexican Restaurant
0                            Albany Park            0.080000
1                        Altgeld Gardens            0.000000
2                          Andersonville            0.018182
3                         Archer Heights            0.136364
4                          Armour Square            0.000000
5                                Ashburn            0.000000
6                        Ashburn Estates            0.000000
7                         Auburn Gresham            0.000000
8                            Avalon Park            0.000000
9                               Avondale            0.000000
10                      Avondale Gardens            0.000000
11                     Back of the Yards            0.058824
12                       Belmont Central            0.117647
13                       Belmont Gardens            0.000000
14                       Belmont Heights            0.000000
15                       Belmont Terrace            0.000000
16                               Beverly            0.000000
17                          Beverly View            0.000000
18                         Beverly Woods            0.111111
19                              Big Oaks            0.010000
20                           Bowmanville            0.000000
21                              Boystown            0.071429
22                              Brainerd            0.000000
23                             Brickyard            0.023256
24                            Bridgeport            0.000000
25                         Brighton Park            0.187500
26                           Bronzeville            0.000000
27                              Bucktown            0.000000
28                         Budlong Woods            0.010000
29                            Buena Park            0.044444
30                              Burnside            0.000000
31                         Cabrini–Green            0.000000
32                       Calumet Heights            0.125000
33                           Canaryville            0.000000
34                       Central Station            0.000000
35                               Chatham            0.000000
36                          Chicago Lawn            0.176471
37                             Chinatown            0.000000
38                      Chrysler Village            0.000000
39                        Clarendon Park            0.023256
40                         Clearing East            0.000000
41                         Clearing West            0.000000
42                 Cottage Grove Heights            0.000000
43                                Cragin            0.250000
44                             Crestline            0.142857
45                        Dearborn Homes            0.000000
46                         Dearborn Park            0.000000
47                          Douglas Park            0.000000
48                               Dunning            0.000000
49                          East Beverly            0.000000
50                          East Chatham            0.000000
51                    East Garfield Park            0.000000
52                        East Hyde Park            0.000000
53                           East Pilsen            0.152542
54                             East Side            0.000000
55                          East Village            0.115942
56                            Eden Green            0.000000
57                             Edgebrook            0.000000
58                             Edgewater            0.071429
59                       Edgewater Beach            0.047619
60                        Edgewater Glen            0.042553
61                           Edison Park            0.000000
62                             Englewood            0.062500
63                              Fernwood            0.000000
64                            Fifth City            0.000000
65

In [127]:
kclusters = 3

chicago_clustering = chicago_new.drop(["Neighborhood"], 1)
chicago_clustering.head()

# run k-means clustering
kmeans = KMeans(init="k-means++", n_clusters=kclusters, n_init=12).fit(chicago_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 0, 0, 2, 0, 0, 0, 0, 0, 0])

In [128]:
merged = chicago_new.copy()

# add clustering labels
merged["Category"] = kmeans.labels_

merged.head()

Neighborhood  Mexican Restaurant  Category
0      Albany Park            0.080000         2
1  Altgeld Gardens            0.000000         0
2    Andersonville            0.018182         0
3   Archer Heights            0.136364         2
4    Armour Square            0.000000         0

In [129]:
dfmerged = merged.merge(chicago_df)
dfmerged.head()

#Sort
dfmerged.sort_values(["Category"], inplace=True, ascending=False)
dfmerged

Neighborhood  Mexican Restaurant  Category  \
0                            Albany Park            0.080000         2   
18                         Beverly Woods            0.111111         2   
118                      Lower West Side            0.150000         2   
21                              Boystown            0.071429         2   
223                          West Elsdon            0.200000         2   
87                        Hollywood Park            0.111111         2   
32                       Calumet Heights            0.125000         2   
58                             Edgewater            0.071429         2   
36                          Chicago Lawn            0.176471         2   
55                          East Village            0.115942         2   
104                         Lake Meadows            0.090909         2   
53                           East Pilsen            0.152542         2   
161                            Pill Hill            0.066667         2   
44                             Crestline            0.142857         2   
162                               Pilsen            0.152542         2   
164                       Polish Village            0.090909         2   
203                    Stony Island Park            0.090909         2   
86                               Hermosa            0.142857         2   
25                         Brighton Park            0.187500         2   
85                             Hegewisch            0.100000         2   
12                       Belmont Central            0.117647         2   
79                             Greektown            0.090909         2   
3                         Archer Heights            0.136364         2   
138                         North Austin            0.166667         2   
130                      Mount Greenwood            0.090909         2   
126                        McKinley Park            0.166667         2   
70                              Galewood            0.090909         2   
228                            West Lawn            0.111111         2   
97                                K-Town            0.071429         2   
83                           Hanson Park            0.090909         2   
123                      Marshall Square            0.200000         2   
196                        South Deering            0.500000         1   
117                       Longwood Manor            0.333333         1   
69                             Gage Park            0.375000         1   
115                       Little Village            0.315789         1   
43                                Cragin            0.250000         1   
194                        South Chicago            0.333333         1   
167                       Prairie Shores            0.000000         0   
174                     Ravenswood Manor            0.000000         0   
166     Prairie Avenue Historic District            0.029412         0   
177                         River's Edge            0.000000         0   
171                              Pullman            0.000000         0   
176                           River West            0.000000         0   
168                       Princeton Park            0.000000         0   
165                         Portage Park            0.045455         0   
169                        Printer's Row            0.011111         0   
173                   Ravenswood Gardens            0.000000         0   
172                           Ravenswood            0.050000         0   
170                         Pulaski Park            0.019231         0   
175                          River North            0.000000         0   
158                            Park West            0.000000         0   
163                      Polish Downtown            0.000000         0   
148                               O'Hare            0.011628         0   
137                         Nobl

In [130]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(dfmerged['Latitude'], dfmerged['Longitude'], dfmerged['Neighborhood'], dfmerged['Category']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examining each cluster

### Cluster 1: Neighborhoods with low numbers of Mexican Restaurants

In [131]:
merged.loc[merged['Category'] == 0]

Neighborhood  Mexican Restaurant  Category
1                        Altgeld Gardens            0.000000         0
2                          Andersonville            0.018182         0
4                          Armour Square            0.000000         0
5                                Ashburn            0.000000         0
6                        Ashburn Estates            0.000000         0
7                         Auburn Gresham            0.000000         0
8                            Avalon Park            0.000000         0
9                               Avondale            0.000000         0
10                      Avondale Gardens            0.000000         0
11                     Back of the Yards            0.058824         0
13                       Belmont Gardens            0.000000         0
14                       Belmont Heights            0.000000         0
15                       Belmont Terrace            0.000000         0
16                               Beverly            0.000000         0
17                          Beverly View            0.000000         0
19                              Big Oaks            0.010000         0
20                           Bowmanville            0.000000         0
22                              Brainerd            0.000000         0
23                             Brickyard            0.023256         0
24                            Bridgeport            0.000000         0
26                           Bronzeville            0.000000         0
27                              Bucktown            0.000000         0
28                         Budlong Woods            0.010000         0
29                            Buena Park            0.044444         0
30                              Burnside            0.000000         0
31                         Cabrini–Green            0.000000         0
33                           Canaryville            0.000000         0
34                       Central Station            0.000000         0
35                               Chatham            0.000000         0
37                             Chinatown            0.000000         0
38                      Chrysler Village            0.000000         0
39                        Clarendon Park            0.023256         0
40                         Clearing East            0.000000         0
41                         Clearing West            0.000000         0
42                 Cottage Grove Heights            0.000000         0
45                        Dearborn Homes            0.000000         0
46                         Dearborn Park            0.000000         0
47                          Douglas Park            0.000000         0
48                               Dunning            0.000000         0
49                          East Beverly            0.000000         0
50                          East Chatham            0.000000         0
51                    East Garfield Park            0.000000         0
52                        East Hyde Park            0.000000         0
54                             East Side            0.000000         0
56                            Eden Green            0.000000         0
57                             Edgebrook            0.000000         0
59                       Edgewater Beach            0.047619         0
60                        Edgewater Glen            0.042553         0
61                           Edison Park            0.000000         0
62                             Englewood            0.062500         0
63                              Fernwood            0.000000         0
64                            Fifth City            0.000000         0
65                             Ford City            0.000000         0
66                           Forest Glen            0.000000         0
67                           Fuller Park            0.000000         0
68                 Fulton River District            

### Cluster 2: Neighborhoods with moderate numbers of Mexican restaurants

In [132]:
merged.loc[merged['Category'] == 1]

Neighborhood  Mexican Restaurant  Category
43           Cragin            0.250000         1
69        Gage Park            0.375000         1
115  Little Village            0.315789         1
117  Longwood Manor            0.333333         1
194   South Chicago            0.333333         1
196   South Deering            0.500000         1

### Cluster 3: Neighborhoods with high numbers of Mexican restaurants

In [133]:
merged.loc[merged['Category'] == 2]

Neighborhood  Mexican Restaurant  Category
0          Albany Park            0.080000         2
3       Archer Heights            0.136364         2
12     Belmont Central            0.117647         2
18       Beverly Woods            0.111111         2
21            Boystown            0.071429         2
25       Brighton Park            0.187500         2
32     Calumet Heights            0.125000         2
36        Chicago Lawn            0.176471         2
44           Crestline            0.142857         2
53         East Pilsen            0.152542         2
55        East Village            0.115942         2
58           Edgewater            0.071429         2
70            Galewood            0.090909         2
79           Greektown            0.090909         2
83         Hanson Park            0.090909         2
85           Hegewisch            0.100000         2
86             Hermosa            0.142857         2
87      Hollywood Park            0.111111         2
97              K-Town            0.071429         2
104       Lake Meadows            0.090909         2
118    Lower West Side            0.150000         2
123    Marshall Square            0.200000         2
126      McKinley Park            0.166667         2
130    Mount Greenwood            0.090909         2
138       North Austin            0.166667         2
161          Pill Hill            0.066667         2
162             Pilsen            0.152542         2
164     Polish Village            0.090909         2
203  Stony Island Park            0.090909         2
223        West Elsdon            0.200000         2
228          West Lawn            0.111111         2